**Homework 14**

In [458]:
import numpy as np
import pandas as pd

*Background*

Recall from the last assignment that Logistic Regression was a way to leverage linear regression to perform binary classification. Here we make further modifications to perform multi-class classification. This is  called *Softmax Regression*. 

As in Logistic Regression, the model we create will predict probabilities, and those probabilities will determine class predictions. The predictied probabilities will be a matrix of shape (n,k), where n is the number of observations and k is the number of classes. 

The input to the model is a feature matrix $X$ of shape (n,m), where as usual n is the number of observations, and m is the number of features. The model is then defined by a coefficient matrix of shape (m,k) and an intercept array of shape (k,). 

The first step in finding a matrix of predicted probabilites is to compute the matrix $$t=X \cdot coef + intercept$$ (similar to linear regression, but note the different shapes!). The probability matrix $p$ is obtained from this matrix $t$ by the softmax function:
$$p_i^j=\frac{e^{t_i^j}}{\sum \limits _{j=1} ^k e^{t_i^j}}.$$

To find the coefficient matrix and intercept array we must first preprocess the target array by doing a *one-hot encoding*. That is, we take a vector $y$ of $n$ entries, where each entry is one of $k$ different classes, and convert it to a matrix $Y$ of shape (n,k) whose entries are all 1's and 0's. In $Y$, a 1 in row i, column j indicates that $y_i$ is in category $j$. 

Our goal is to find the coefficent matrix and intercept array so that the probability $p_i^j$ is close to one if $Y_i^j=1$, and close to zero otherwise. In Softmax regression we accomplish this by using gradient descent to minimize the *categorical cross entropy loss*:
$$CE=-\frac{1}{n}\sum \limits _{i,j} Y_i^j Log(p_i^j)$$

With these definitions, the forumlas for the gradient calculation and coefficient/intercept updates are the same as in Logistic Regression. This should not be surprising, as binary Softmax Regression is mathematically identical to Logistic Regression.


Before we define our `SoftmaxRegression()` class, we'll need to create a class that performs the one-hot encoding:

In [459]:
class OneHotEncoder():
    def __init__(self):
        pass
    
    def fit(self,y):
        self.categories= np.unique(y)   #Array of unique categories that appear in y
        self.n_features_in= self.categories.shape[0]     #Number of categories
        
    def transform(self,y):
        Y = np.zeros((y.shape[0],self.n_features_in)) #Create one-hot encoding here (Hint: it's OK to use a for-loop to iterate through categories))
        for i in np.arange(self.n_features_in):
            Y[:, i] = y==self.categories[i]
        return Y
    
    def fit_transform(self,y):
        '''Convenience method that applies fit and then 
        immediately transforms'''
        self.fit(y)
        return self.transform(y)

Test your class here:

In [460]:
y=np.array(['a','b','a','c','b','b'])
encoder=OneHotEncoder()
encoder.fit_transform(y)

array([[1., 0., 0.],
       [0., 1., 0.],
       [1., 0., 0.],
       [0., 0., 1.],
       [0., 1., 0.],
       [0., 1., 0.]])

Defining `OneHotEncoder()` as a class will allow us to fit our encoder to a train set but apply it to a test set:

In [461]:
z=np.array(['b','c','b'])
encoder.transform(z)

array([[0., 1., 0.],
       [0., 0., 1.],
       [0., 1., 0.]])

Note that this is a different result than if we had done `encoder.fit_transform(z)`.

We are now ready to create our `SoftmaxRegression()` class. Below is most of the code from the `LogisticRegression()` class. Modify it appropriately, where indicated. 

In [ ]:
class SoftmaxRegression():
    def __init__(self,learning_rate, max_iter, batch_size, penalty='l2', alpha=0.0001):
        self.lr=learning_rate
        self.max_iter=max_iter 
        self.batch_size=batch_size
        self.penalty=penalty 
        self.alpha=alpha 
        self.encoder=OneHotEncoder() 
        
    def fit(self,X,y):
        Y=self.encoder.fit_transform(y)
        # print(Y.shape, X.shape)
        self.coef=np.ones((X.shape[1], Y.shape[1])) # number of features x number of categories
        self.intercept=np.ones(Y.shape[1],) 
        if self.penalty=='l1':
            penalty_grad=lambda x:2*(x>0)-1
        elif self.penalty=='l2':
            penalty_grad=lambda x:x

        indices=np.arange(len(X))
        for i in range(self.max_iter):
            np.random.seed(i) 
            np.random.shuffle(indices)
            X_shuffle=X[indices] 
            Y_shuffle=Y[indices] 
            for j in range(0,len(X),self.batch_size):
                X_batch=X_shuffle[j:j+self.batch_size]
                Y_batch=Y_shuffle[j:j+self.batch_size] #Note that we're using Y here, not y
                # print("self.predict_proba(X_batch)", end=" "); print(self.predict_proba(X_batch).shape)
                # # print("self.predict_proba(X_batch)", end=" "); print(X_batch.shape)
                # print("Y_batch", end=" "); print(Y_batch.shape)
                residuals=self.predict_proba(X_batch)-Y_batch 
                coef_grad=(X_batch.T)@residuals/len(X_batch)
                intercept_grad=np.mean(residuals)
                self.coef-=self.lr*coef_grad+self.alpha*penalty_grad(self.coef)
                self.intercept-=self.lr*intercept_grad+self.alpha*penalty_grad(self.intercept)
            
    def predict_proba(self,X):
        '''returns the matrix of predicted probabilites'''
        # print("X", end=" "); print(X.shape)
        # print("coef", end=" "); print(self.coef.shape)

        T = X@self.coef + self.intercept
        # print(div)
        print("T",T.shape)
        print("sum shape", np.sum(np.exp(T), axis=1).shape)
        print(np.exp(T)/np.sum(np.exp(T), axis=1)[:,np.newaxis])
        return np.exp(T)/np.sum(np.exp(T), axis=1)[:,np.newaxis]
    
    def predict(self,X):
        '''returns a prediction, for each observation in X, 
        of one category.'''
        preds = self.predict_proba(X)
        return np.argmax(preds, axis=1)
    
    def score(self,X,y): 
        '''returns accuracy of the model'''
        print(y)
        predictions = self.predict(X)
        predictions = np.unique(y)[predictions]
        print(predictions)
        return (predictions==y).mean() #Unchanged from Logistic Regression
    
    def CEloss(self,X,y): #Not a sklearn method!
        '''returns the Categorical Cross Entropy loss'''
        preds = self.predict_proba(X)
        # print(preds)
        # print(y[:,np.newaxis])
        Y = self.encoder.fit_transform(y)
        print(Y)
        # return np.sum(Y[:,np.newaxis]* np.log(preds))/Y.shape[0]
        return -np.sum(Y[:,np.newaxis]* np.log(preds))/Y.shape[0]

Note that we have departed here from `sklearn` syntax. To perform Softmax Regression with that package, call the `LogisticRegression()` class and set `multi_class=multinomial`.

We'll now test your `SoftmaxRegression()` class on some real data. To keep things realistic, we should first do a train/test split, so we'll need to bring back this function:

In [463]:
def TrainTestSplit(x,y,p,seed=4):
    '''Splits datasets x and y into train and test sets
    p is the fraction going to train'''
    rng = np.random.default_rng(seed=seed)#Don't change seed!
    size=len(x)
    train_size=int(p*size)
    train_mask=np.zeros(size,dtype=bool)
    train_indices=rng.choice(size, train_size, replace=False)  
    train_mask[train_indices]=True
    test_mask=~train_mask
    x_train=x[train_mask]
    x_test=x[test_mask]
    y_train=y[train_mask]
    y_test=y[test_mask]
    return x_train,x_test,y_train,y_test

We'll now test your `SoftmaxRegression()` class on the iris dataset:

In [464]:
iris=(pd.read_csv('https://vincentarelbundock.github.io/Rdatasets/csv/datasets/iris.csv',index_col=0))
X=np.array(iris.loc[:,'Sepal.Length':'Petal.Width'])
y=np.array(iris['Species'])

In [465]:
iris.head

<bound method NDFrame.head of           Sepal.Length  Sepal.Width  Petal.Length  Petal.Width    Species
rownames                                                                 
1                  5.1          3.5           1.4          0.2     setosa
2                  4.9          3.0           1.4          0.2     setosa
3                  4.7          3.2           1.3          0.2     setosa
4                  4.6          3.1           1.5          0.2     setosa
5                  5.0          3.6           1.4          0.2     setosa
...                ...          ...           ...          ...        ...
146                6.7          3.0           5.2          2.3  virginica
147                6.3          2.5           5.0          1.9  virginica
148                6.5          3.0           5.2          2.0  virginica
149                6.2          3.4           5.4          2.3  virginica
150                5.9          3.0           5.1          1.8  virginica

[150 ro

In [466]:
np.unique(y)

array(['setosa', 'versicolor', 'virginica'], dtype=object)

Again, do an 80/20 train/test split. As this dataset is much smaller, your test set will only contain 30 observations. 

In [467]:
Xtrain,Xtest,ytrain,ytest= TrainTestSplit(X, y, .80)

In [468]:
X.shape, Xtrain.shape

((150, 4), (120, 4))

Create a Softmax Regression object with a learning rate of 0.01, which trains for 1000 epochs with batches of size of 50, and no regularization. Then, fit it to `Xtrain` and `ytrain`. 

In [469]:
mod= SoftmaxRegression(learning_rate=0.01, max_iter=1000, batch_size=50, alpha=0)
mod.fit(Xtrain, ytrain)

T (50, 3)
sum shape (50,)
[[0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [0.33333333 0.33333333 0.33333333]
 [

Check the accuracy on the test set:

In [470]:
accuracy= mod.score(Xtest, ytest)
accuracy

['setosa' 'setosa' 'setosa' 'setosa' 'setosa' 'setosa' 'setosa' 'setosa'
 'setosa' 'versicolor' 'versicolor' 'versicolor' 'versicolor' 'versicolor'
 'versicolor' 'versicolor' 'versicolor' 'versicolor' 'versicolor'
 'virginica' 'virginica' 'virginica' 'virginica' 'virginica' 'virginica'
 'virginica' 'virginica' 'virginica' 'virginica' 'virginica']
T (30, 3)
sum shape (30,)
[[9.69634425e-01 3.03527959e-02 1.27786352e-05]
 [9.32400215e-01 6.75417374e-02 5.80477900e-05]
 [9.59902683e-01 4.00555349e-02 4.17825168e-05]
 [9.67902996e-01 3.20882884e-02 8.71583204e-06]
 [9.76674025e-01 2.33148967e-02 1.10783899e-05]
 [9.64655455e-01 3.53306975e-02 1.38477693e-05]
 [9.90508020e-01 9.49075553e-03 1.22443587e-06]
 [9.30955158e-01 6.89794584e-02 6.53838597e-05]
 [9.49318190e-01 5.06233125e-02 5.84978811e-05]
 [1.88614930e-02 8.40684491e-01 1.40454016e-01]
 [1.45475347e-02 5.29076062e-01 4.56376404e-01]
 [3.59457254e-02 8.33932769e-01 1.30121506e-01]
 [8.32322015e-03 4.15541972e-01 5.76134807e-01]
 

0.9666666666666667

Multiplying this by 30 (the size of the test set) will reveal how many predictions were correct:

In [471]:
accuracy*30

29.0

List all 30 species that your model predicts from `Xtest`. (If you compare this to `ytest`, you would be able to determine which flower species the model had trouble with.)

In [472]:
predictions= mod.predict(Xtest)
predictions = np.unique(ytrain)[predictions]
predictions

T (30, 3)
sum shape (30,)
[[9.69634425e-01 3.03527959e-02 1.27786352e-05]
 [9.32400215e-01 6.75417374e-02 5.80477900e-05]
 [9.59902683e-01 4.00555349e-02 4.17825168e-05]
 [9.67902996e-01 3.20882884e-02 8.71583204e-06]
 [9.76674025e-01 2.33148967e-02 1.10783899e-05]
 [9.64655455e-01 3.53306975e-02 1.38477693e-05]
 [9.90508020e-01 9.49075553e-03 1.22443587e-06]
 [9.30955158e-01 6.89794584e-02 6.53838597e-05]
 [9.49318190e-01 5.06233125e-02 5.84978811e-05]
 [1.88614930e-02 8.40684491e-01 1.40454016e-01]
 [1.45475347e-02 5.29076062e-01 4.56376404e-01]
 [3.59457254e-02 8.33932769e-01 1.30121506e-01]
 [8.32322015e-03 4.15541972e-01 5.76134807e-01]
 [1.12170601e-02 7.12890348e-01 2.75892591e-01]
 [3.43738410e-02 7.90381250e-01 1.75244909e-01]
 [1.96333805e-02 8.09245390e-01 1.71121230e-01]
 [1.72551900e-02 7.02624295e-01 2.80120515e-01]
 [3.29320170e-02 8.02365669e-01 1.64702314e-01]
 [3.23869042e-02 7.31344720e-01 2.36268376e-01]
 [4.22907464e-04 2.33909147e-01 7.65667945e-01]
 [4.70831849e-

array(['setosa', 'setosa', 'setosa', 'setosa', 'setosa', 'setosa',
       'setosa', 'setosa', 'setosa', 'versicolor', 'versicolor',
       'versicolor', 'virginica', 'versicolor', 'versicolor',
       'versicolor', 'versicolor', 'versicolor', 'versicolor',
       'virginica', 'virginica', 'virginica', 'virginica', 'virginica',
       'virginica', 'virginica', 'virginica', 'virginica', 'virginica',
       'virginica'], dtype=object)

Check the cross entropy loss on the test data. (This won't be very meaningful on its own, but would be useful in comparing the effects of different choices of `max_iter`, `batch_size`, learning rate, and amount of regularization.)

In [473]:
loss=mod.CEloss(Xtest, ytest)
loss

T (30, 3)
sum shape (30,)
[[9.69634425e-01 3.03527959e-02 1.27786352e-05]
 [9.32400215e-01 6.75417374e-02 5.80477900e-05]
 [9.59902683e-01 4.00555349e-02 4.17825168e-05]
 [9.67902996e-01 3.20882884e-02 8.71583204e-06]
 [9.76674025e-01 2.33148967e-02 1.10783899e-05]
 [9.64655455e-01 3.53306975e-02 1.38477693e-05]
 [9.90508020e-01 9.49075553e-03 1.22443587e-06]
 [9.30955158e-01 6.89794584e-02 6.53838597e-05]
 [9.49318190e-01 5.06233125e-02 5.84978811e-05]
 [1.88614930e-02 8.40684491e-01 1.40454016e-01]
 [1.45475347e-02 5.29076062e-01 4.56376404e-01]
 [3.59457254e-02 8.33932769e-01 1.30121506e-01]
 [8.32322015e-03 4.15541972e-01 5.76134807e-01]
 [1.12170601e-02 7.12890348e-01 2.75892591e-01]
 [3.43738410e-02 7.90381250e-01 1.75244909e-01]
 [1.96333805e-02 8.09245390e-01 1.71121230e-01]
 [1.72551900e-02 7.02624295e-01 2.80120515e-01]
 [3.29320170e-02 8.02365669e-01 1.64702314e-01]
 [3.23869042e-02 7.31344720e-01 2.36268376e-01]
 [4.22907464e-04 2.33909147e-01 7.65667945e-01]
 [4.70831849e-

92.34294639955804

What does your model say that the probability of a flower with Sepal Length 4, Sepal Width 3, Petal Length 2, and Petal Width 1 is of being a setosa?

In [474]:
# idea: use predict proba function on a flower with given characteristics
# Setosa flower stored probability stored at 0th index of the return 

flower = np.array([4.,3.,2.,1.])
setosa_prob = 0
# setosa_prob=mod.predict_proba(flower)
setosa_prob

0